# Sampling from distributions
Now that we are able to sample equally distributed (pseudo-)random numbers in the interval $[1, 0)$, we now able to sample random numbers from arbitrary distributions.

## Setup

In [ ]:
%matplotlib inline
import numpy as np
import scipy as sp
import matplotlib.pyplot as plt

## Rejection sampling
The most simple method to generate random numbers from a distribution is called rejection sampling. This method is generally easy to implement, but can be very slow depending on the sampled distribution. Further info can be found at [Wikipedia](https://en.wikipedia.org/wiki/Rejection_sampling).

Assume we want to sample data from a probability density function $f$. Assume further we are able to generate random numbers according to a distribution $g$. Also, we have a bound $M$ (a function envoloping $f$), so that $f(x) < Mg(x)~\forall~x$.

Then we can sample random numbers distributed like f:
1. Sample a random number $u \in [0,1)$
2. Sample a random number $x$ from $g(x)$
3. Calculate $\Delta = \frac{f(x)}{Mg(x)} - u$

If $\Delta \geq 0$, $x$ is distributed according to $f$, and we return the random number $x$. Else, we reject the result and repeat the process.

For example, we can use equally distributed random numbers in an interval $[a, b]$, and select an $M$ so that $g(x) = 1 ~\forall~x \in [a, b)$. In practice, we can just set $g(x) = M = 1$.

So let's write the code to implement what we described above:

In [ ]:
def gauss(x, mu=0., sigma=1.):
    return 1./(sigma * np.sqrt(2.*np.pi)) * np.exp(-0.5 * ( 1.*(x-mu) / sigma)**2)

def draw_one_sample(func, a=0., b=1., M=1., *funcargs, **funckwargs):
    # generate uniformly distributed random number in the interval [a, b)
    x = (b-a) * np.random.random() + a
    # generate uniformly distributed random number in the interval [0,1]
    u = np.random.random() * M
    # calculate delta
    delta = 1.*func(x, *funcargs, **funckwargs) - u
    return x, u, delta

def rejection_sampler(func, a=0., b=1., M=1., *funcargs, **funckwargs):
    delta = -1
    x = 0
    while not delta >= 0:
        x, u, delta = draw_one_sample(func, a, b, M, *funcargs, **funckwargs)
    return x


# limit the range of sampling
# choosing larger intervals increases computing time due to more rejections
x = np.arange(-20.,20.,0.01)
a = x[0]
b = x[-1]
M = 0.6 # gaussian distribution does not exceed 0.6
r = np.array([rejection_sampler(gauss, a, b, M) for i in range(50000)])


# plot the histogram of the sampled numbers
h, xb = np.histogram(r, bins=1000, density=True)
plt.plot(xb[:-1]+np.diff(xb), h, color='C0', label='Rejection sampled normal distribution');

# overplot the calculated gauss
x = np.arange(-6.,6.,0.01)
y = gauss(x)
plt.plot(x,y, color='C1', label='Normal distribution');

# show an example of accepted and rejected samples
r_e = np.array([draw_one_sample(gauss, a, b, M) for i in range(1500)])
x, y, delta = r_e.T
plt.plot(x[delta<0], y[delta<0], linestyle='', marker='x', color='C2', label="Miss")
plt.plot(x[delta>=0], y[delta>=0], linestyle='', marker='o', color='C1', label="Hit")

# prettify
plt.xlabel("x")
plt.ylabel("p")
plt.ylim(0., 0.9)
plt.xlim(-6.,6.)
plt.legend();

The algorithm works well, but as we can see is quite slow. The main reason is that on the "wings" the probability approaches zero fast, which means we reject a lot of random numbers. For every rejection we will have to call the function again. Thus, the runtime of this sampling method depends strongly on the similarity of the envelope distribution and the distribution to be sampled, and the chosen interval.

## Inversion sampling
The other widespread used method to sample random numbers is inversion sampling. Info on that can also be found at [Wikipeda](https://en.wikipedia.org/wiki/Inverse_transform_sampling).

We have to able to generate uniformly distributed random numbers in the interval $[0,1)$.

Assume we want to take random samples distributed like a known continuous distribution function $F(x)$.  We have to do the following steps:

1. Normalize F: $\int_{-\infty}^{\infty} F(x) \mathrm{d}x = N$, to calculate the probability density function (PDF) $f(x) = F(x)/N$
2. Calculate the cumulative distribution function (CDF) $C(x) = \int_{-\infty}^{x} f(x') \mathrm{d}x'$
3. Calculate the inverse CDF (iCDF). This assumes that $C(x)$ can be inverted (i.e. solved for $x$), so that we get a function $X(u)$
4. Sample a uniformly distributed random number $u$ in the interval $[0,1)$
5. Calculate $x=X(u)$. The generated $x$s will be distributed according to the probability density function $f(x)$

Let's implement the algorithm and inspect all the steps and generate random numbers according to an exponential distribution. The PDF of an exponential distribution is $f(x) = \lambda \exp\left(-\lambda x\right)$, and it's defined on the interval $[0, \infty)$

In [ ]:
x = np.arange(0,15,0.001)

In [ ]:
def expon(x, l=1.):
    return l * np.exp(-l * x)

plt.plot(x, expon(x), label="Exponential distribution PDF");
plt.legend();

The CDF of the exponential distribution is $C(x) = 1 - \exp\left(-\lambda x\right)$

In [ ]:
def expon_c(x, l=1.):
    return 1. - np.exp(-l * x)

plt.plot(x, expon_c(x), label="Exponential distribution CDF");
plt.legend();

We can see nicely that the cumulative distribution function does not exceed $1$. We can already see that if we invert the CDF $C(x)$ and sample values on the y-axis, we can generate the values on the x-axis.

The iCDF is $X(u) = -\frac{1}{\lambda} \ln \left(1-u\right)$.

In [ ]:
def expon_ic(u, l=1.):
    return -1./l * np.log(1. - u)

u = np.arange(0., 1., 0.001)
plt.plot(u, expon_ic(u), label="Exponential distribution iCDF");
plt.legend();

We can now write our random number generator, which creates numbers according to the exponential distribution, and try it out.

In [ ]:
def rand_expon(l=1.):
    u = np.random.random()
    return expon_ic(u, l)

r = np.array([rand_expon() for i in range(200000)])

h, xb = np.histogram(r, bins=1000, density=True)
plt.plot(xb[:-1]+np.diff(xb), h, color='b', label='Inversion sampled exponential distribution');

plt.plot(x, expon(x), color='r', label='Exponential distribution');
plt.legend();

Let's compare the runtime of the inversion sampling method, to the runtime of the rejection sampling method. We can already see that it is very impractical to generate random numbers up to $\infty$ using rejection sampling. We compare both methods for different interval lengths.

In [ ]:
import time

def rand_expon_interval(a=0, b=np.inf, l=1.):
    r = -1
    while not (a <= r < b):
        r = rand_expon(l)
    return r    

for b in np.linspace(5., 25., 5.):
    print("b=%.2f"%b)
    a=0.

    start = time.time()
    inv = [rand_expon_interval(a,b) for i in range(20000)]
    end = time.time()
    print("Time to generate 20000 numbers using inversion sampling: %f"%(end-start))

    start = time.time()
    inv = [rejection_sampler(expon, a=a, b=b, M=1.0001) for i in range(20000)]
    end = time.time()
    print("Time to generate 20000 numbers using rejection sampling: %f"%(end-start))
    print()

We can see that this method is much faster than rejection sampling, because the exponential function drops off very fast.

### Inversion sampling of discrete (measured) distributions
In case we only have access to a discrete representation of a distribution, for example data measured by an instrument, we can also perform inversion sampling, though in a discrete fashion. The steps are basically the same as above, we just replace the analytical methods with numerical ones. Assume we have measured data which is distributed according to a distribution function $F(x)$, in discrete bins $x_0, x_1, \ldots x_n$

1. Normalize $F(x)$, $N= \sum_{i=0}^{N} F(x_i)$, then calculate the probability density function $f(x) = \frac{F(x)}{N}$
2. Determine the CDF $C(x)$ as cumulative sum of $f(x)$: $C(x) = \sum_{i=0}^{x} f(x_i)$
3. Sample a uniform random number $u$ in $[0,1)$.
4. Sort $u$ into $C(x)$, and store the index $t$, i.e. calculate the histogram of all $u$s.
5. The histogram generated in step 4 is distributed like $F$.

Let's implement this now. We have already sampled values form the normal distribution, so we now histogram those values to generate an *artifical* measurement.

In [ ]:
r = [np.random.randn(5000)]
bins = np.linspace(-3,3,31)
h, xb = np.histogram(r, bins=bins)
x = xb[:-1] + 0.5 * np.diff(xb)

plt.plot(x, h);

In [ ]:
f = 1.* h / h.sum()

plt.plot(x,f);

In [ ]:
c = f.cumsum()

plt.plot(x,c);

In [ ]:
u = np.random.random(5000)

cbins = np.concatenate(([0],c))

h2, cb = np.histogram(u, bins=cbins)

plt.plot(x, h, label="Measurement data");
plt.plot(x, h2,label="Random samples from measurement data");
plt.ylim(0, h.max()*1.4)
plt.legend();